.
.
.
.
.


In [1]:
import plotly.graph_objs as go
import plotly.express as px
import pandas as pd
import numpy as np
import scipy
import plotly.figure_factory as ff

ModuleNotFoundError: No module named 'scipy'

In [158]:
energy_df = pd.read_csv('energy_dataset.csv').drop(['generation hydro pumped storage aggregated', 'generation marine', 'forecast wind offshore eday ahead'], axis=1)
energy_df.head()

time  generation biomass  \
0  2015-01-01 00:00:00+01:00               447.0   
1  2015-01-01 01:00:00+01:00               449.0   
2  2015-01-01 02:00:00+01:00               448.0   
3  2015-01-01 03:00:00+01:00               438.0   
4  2015-01-01 04:00:00+01:00               428.0   

   generation fossil brown coal/lignite  generation fossil coal-derived gas  \
0                                 329.0                                 0.0   
1                                 328.0                                 0.0   
2                                 323.0                                 0.0   
3                                 254.0                                 0.0   
4                                 187.0                                 0.0   

   generation fossil gas  generation fossil hard coal  generation fossil oil  \
0                 4844.0                       4821.0                  162.0   
1                 5196.0                       4755.0                  158.0   
2                 4857.0                       4581.0                  157.0   
3                 4314.0                       4131.0                  160.0   
4                 4130.0                       3840.0                  156.0   

   generation fossil oil shale  generation fossil peat  generation geothermal  \
0                          0.0                     0.0                    0.0   
1                          0.0                     0.0                    0.0   
2                          0.0                     0.0                    0.0   
3                          0.0                     0.0                    0.0   
4                          0.0                     0.0                    0.0   

   ...  generation solar  generation waste  generation wind offshore  \
0  ...              49.0             196.0                       0.0   
1  ...              50.0             195.0                       0.0   
2  ...              50.0             196.0                       0.0   
3  ...              50.0             191.0                       0.0   
4  ...              42.0             189.0                       0.0   

   generation wind onshore  forecast solar day ahead  \
0                   6378.0                      17.0   
1                   5890.0                      16.0   
2                   5461.0                       8.0   
3                   5238.0                       2.0   
4                   4935.0                       9.0   

   forecast wind onshore day ahead  total load forecast  total load actual  \
0                           6436.0              26118.0            25385.0   
1                           5856.0              24934.0            24382.0   
2                           5454.0              23515.0            22734.0   
3                           5151.0              22642.0            21286.0   
4                           4861.0              21785.0            20264.0   

   price day ahead  price actual  
0            50.10         65.41  
1            48.10         64.92  
2            47.33         64.48  
3            42.27         59.32  
4            38.41         56.04  

[5 rows x 26 columns]

In [159]:
li = range(13)
weather_df = pd.read_csv('weather_features.csv', usecols=li).drop('city_name', axis=1)
weather_df = weather_df.groupby('time').mean()
weather_df.head()


temp    temp_min    temp_max  pressure  \
time                                                                      
2015-01-01 00:00:00+01:00  272.491463  272.491463  272.491463    1016.4   
2015-01-01 01:00:00+01:00  272.512700  272.512700  272.512700    1016.2   
2015-01-01 02:00:00+01:00  272.099137  272.099137  272.099137    1016.8   
2015-01-01 03:00:00+01:00  272.089469  272.089469  272.089469    1016.6   
2015-01-01 04:00:00+01:00  272.145900  272.145900  272.145900    1016.6   

                           humidity  wind_speed  wind_deg  rain_1h  rain_3h  \
time                                                                          
2015-01-01 00:00:00+01:00      82.4         2.0     135.2      0.0      0.0   
2015-01-01 01:00:00+01:00      82.4         2.0     135.8      0.0      0.0   
2015-01-01 02:00:00+01:00      82.0         2.4     119.0      0.0      0.0   
2015-01-01 03:00:00+01:00      82.0         2.4     119.2      0.0      0.0   
2015-01-01 04:00:00+01:00      82.0         2.4     118.4      0.0      0.0   

                           snow_3h  clouds_all  
time                                            
2015-01-01 00:00:00+01:00      0.0         0.0  
2015-01-01 01:00:00+01:00      0.0         0.0  
2015-01-01 02:00:00+01:00      0.0         0.0  
2015-01-01 03:00:00+01:00      0.0         0.0  
2015-01-01 04:00:00+01:00      0.0         0.0

In [160]:
df_whole = weather_df.merge(energy_df, on='time')
df = df_whole[:8760]
times = []
for time in df['time']:
    good, bad = time.split('+')
    times.append(good)
df['time']= times
df.head()

time        temp    temp_min    temp_max  pressure  \
0  2015-01-01 00:00:00  272.491463  272.491463  272.491463    1016.4   
1  2015-01-01 01:00:00  272.512700  272.512700  272.512700    1016.2   
2  2015-01-01 02:00:00  272.099137  272.099137  272.099137    1016.8   
3  2015-01-01 03:00:00  272.089469  272.089469  272.089469    1016.6   
4  2015-01-01 04:00:00  272.145900  272.145900  272.145900    1016.6   

   humidity  wind_speed  wind_deg  rain_1h  rain_3h  ...  generation solar  \
0      82.4         2.0     135.2      0.0      0.0  ...              49.0   
1      82.4         2.0     135.8      0.0      0.0  ...              50.0   
2      82.0         2.4     119.0      0.0      0.0  ...              50.0   
3      82.0         2.4     119.2      0.0      0.0  ...              50.0   
4      82.0         2.4     118.4      0.0      0.0  ...              42.0   

   generation waste  generation wind offshore  generation wind onshore  \
0             196.0                       0.0                   6378.0   
1             195.0                       0.0                   5890.0   
2             196.0                       0.0                   5461.0   
3             191.0                       0.0                   5238.0   
4             189.0                       0.0                   4935.0   

   forecast solar day ahead  forecast wind onshore day ahead  \
0                      17.0                           6436.0   
1                      16.0                           5856.0   
2                       8.0                           5454.0   
3                       2.0                           5151.0   
4                       9.0                           4861.0   

   total load forecast  total load actual  price day ahead  price actual  
0              26118.0            25385.0            50.10         65.41  
1              24934.0            24382.0            48.10         64.92  
2              23515.0            22734.0            47.33         64.48  
3              22642.0            21286.0            42.27         59.32  
4              21785.0            20264.0            38.41         56.04  

[5 rows x 37 columns]

In [161]:
sum_biomass = df['generation biomass'].sum()
sum_coal = df['generation fossil brown coal/lignite'].sum()
sum_gas = df['generation fossil gas'].sum()
sum_hard_coal = df['generation fossil hard coal'].sum()
sum_oil = df['generation fossil oil'].sum()
sum_hydro = df['generation hydro pumped storage consumption'].sum() + df['generation hydro run-of-river and poundage'].sum() + df['generation hydro water reservoir'].sum()
sum_nuclear = df['generation nuclear'].sum()
sum_other = df['generation other'].sum() + df['generation other renewable'].sum() + df['generation waste'].sum() + df['generation fossil oil'].sum() + df['generation fossil brown coal/lignite'].sum() + df['generation biomass'].sum()
sum_solar = df['generation solar'].sum()
sum_waste = df['generation waste'].sum()
sum_wind = df['generation wind onshore'].sum()


labels = ['Gas', 'Hard coal', 'Hydro', 'Nuclear', 'Other', 'Solar', 'Wind']
values = [sum_gas, sum_hard_coal, sum_hydro, sum_nuclear, sum_other, sum_solar, sum_wind]
layout = go.Layout(
    height=600,
    title='Sold houses in the Netherlands, by type, in 2017',
    showlegend=False,
    hovermode=False,

)

fig = go.Figure(data=[go.Pie(labels=labels, values=values, hole=.8, textinfo='label + percent', marker=dict(colors=px.colors.qualitative.T10), textposition='outside')], layout=layout)

fig.show()


In [162]:
df['date'] = pd.to_datetime(df['time'])


fig = px.scatter(df, x=df['wind_speed'], y=df['generation wind onshore'], color=df['price actual'], opacity=1, animation_frame=df['date'].dt.month_name())
fig.layout.updatemenus[0].buttons[0].args[1]['frame']['duration'] = 3000

fig.show()

.
.
.
.
.
.
.
.
.
.


In [163]:
values_wind = df['generation wind onshore']
total = df['total load actual']
values_coal = df['generation fossil hard coal']
values_nuclear = df['generation nuclear']

wind_percentages = []
coal_percentages = []
nuclear_percentages = []
for i in range(len(values_coal)):
    if 0<values_wind[i]/total[i]<1:
        wind_percentages.append(values_wind[i]/total[i])
    else:
        wind_percentages.append(0)
    if 0<values_coal[i]/total[i]<1:
        coal_percentages.append(values_coal[i]/total[i])
    else:
        coal_percentages.append(0)
    if 0<values_nuclear[i]/total[i]<1:
        nuclear_percentages.append(values_nuclear[i]/total[i])
    else:
        nuclear_percentages.append(0)
df_2= pd.DataFrame(data =[wind_percentages, coal_percentages, nuclear_percentages]).T
df_2.columns=['wind', 'coal', 'nuclear']

smoothed_values_wind = df_2['wind'].rolling(365, min_periods=1, center=True).mean()
smoothed_values_coal = df_2['coal'].rolling(365, min_periods=1, center=True).mean()
smoothed_values_nuclear = df_2['nuclear'].rolling(365, min_periods=1, center=True).mean()

fig = go.Figure()
fig.add_trace(go.Scatter(x=df['time'], y=smoothed_values_wind, name='Percentage wind energy', line=dict(color='blue')))
fig.add_trace(go.Scatter(x=df['time'], y=smoothed_values_coal, name='Percentage coal energy', line=dict(color='orange')))

fig.update_layout(title='Percentage contribution of total energy used', hovermode=False)
fig.show()
# fig = px.line(x=df['time'], y=smoothed_values, title='Life expectancy in Canada')
# fig.show()

In [164]:

color_wind = 'blue'
color_nuclear = 'orange'
fig = go.Figure()
fig.add_trace(go.Box(y=df['generation wind onshore'], name='Wind energy generated', marker_color=color_wind))
fig.add_trace(go.Box(y=df['generation nuclear']*df['generation wind onshore'].mean()/df['generation nuclear'].mean(), name='Nuclear energy generated', marker_color=color_nuclear))
fig.update_layout(hovermode=False, showlegend=False, title='Distribution of wind and nuclear energy scaled to the same average')


In [165]:
color_wind = 'blue'
color_nuclear = 'orange'
color_hydro = 'pink'
fig = go.Figure()
fig.add_trace(go.Box(y=df['generation wind onshore'], name='Wind energy generated', marker_color=color_wind))
fig.add_trace(go.Box(y=df['generation solar']*df['generation wind onshore'].mean()/df['generation solar'].mean(), name='Solar energy generated', marker_color=color_nuclear))
fig.add_trace(go.Box(y= df['generation hydro water reservoir'] * df['generation wind onshore'].mean() / df['generation hydro water reservoir'].mean(), name='Hydro energy generated', marker_color=color_hydro))
fig.update_layout(hovermode=False, showlegend=False, title='Distribution of wind and solar energy scaled to the same average')
fig.show()

In [166]:
smoothed_values_wind = df['generation wind onshore'].rolling(365, min_periods=1, center=True).mean()
smoothed_values_solar = df['generation solar'].rolling(365, min_periods=1, center=True).mean()
smoothed_values_hydro = df['generation hydro water reservoir'].rolling(365, min_periods=1, center=True).mean()

fig = go.Figure()
fig.add_trace(go.Scatter(x=df['time'], y=smoothed_values_wind, name='Percentage wind energy', line=dict(color='blue')))
fig.add_trace(go.Scatter(x=df['time'], y=smoothed_values_solar, name='Percentage solar energy', line=dict(color='orange')))
fig.add_trace(go.Scatter(x=df['time'], y=smoothed_values_hydro, name='Percentage hydro energy', line=dict(color='pink')))


fig.update_layout(title='Percentage contribution of total energy used', hovermode=False)
fig.show()
